<a href="https://colab.research.google.com/github/AntikGhalt/predicting_bankruptcy_AIDA/blob/main/AIDA_2_TEST2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


### COLAB DRIVE

---



In [33]:
#@title RESET AND FILES NAME
%reset -f
#path data export
model_folder = "model_test/"

# list your files in the exact order you want their rows to appear
file_names = [
    "Aida_Export_TESTin_0_1000.xlsx",
    "Aida_Export_TESTout_100001_101000.xlsx",
]

test_files = [
    "Aida_Export_testD_001_200.xlsx",
    "Aida_Export_testD_201_400.xlsx",
    "Aida_Export_testD_401_600.xlsx",
    "Aida_Export_testD_601_800.xlsx",
    "Aida_Export_testD_801_1000.xlsx",
    "Aida_Export_testD_100001_100100.xlsx",
    "Aida_Export_testD_100101_100200.xlsx",
    "Aida_Export_testD_100201_100400.xlsx",
    "Aida_Export_testD_100401_100600.xlsx",
    "Aida_Export_testD_100601_100800.xlsx",
    "Aida_Export_testD_100801_101000.xlsx"
]

In [34]:
path_data = "/content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/DATA/" + model_folder
path_MODEL = "/content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/output/" + model_folder

In [35]:
from IPython.display import clear_output
!pip install pandas
#!pip install scikit-learn
#!pip install optuna

import pandas as pd
import os
import numpy as np
import re

"""
def safe_literal_eval(x):
    # If x is a list or numpy array and empty, return an empty list
    if isinstance(x, (list, np.ndarray)) and len(x) == 0:
        return []
    # For scalar values, check if x is NaN
    if not isinstance(x, (list, np.ndarray)) and pd.isna(x):
        return []

    # Otherwise, convert to string and strip any whitespace
    x = str(x).strip()

    try:
        return ast.literal_eval(x)
    except Exception:
        return x
"""
clear_output()

### DATA MANIPULATION

---




In [36]:
#@title FILES ≥ 15 (with per–chunk date/year fixing)

# 1) Regex for “year” or “date” at end of column name
date_pattern = re.compile(r'(year|date)$', re.IGNORECASE)

df_list = []
for fn in file_names:               # assumes file_names & path_data exist
    print(f"Processing file: {fn}")
    tmp = pd.read_excel(
        path_data + fn,
        sheet_name="Results",
        index_col=None,
        na_values=["n.a."],       # if you still have literal "n.a."
        keep_default_na=True
    )
    # 2) Normalize your key
    tmp['Tax code number'] = tmp['Tax code number'].astype('Int64')

    # 3) Find & fix every date/year column in this chunk
    for col in tmp.columns:
        if not date_pattern.search(col):
            continue

        ser = tmp[col]
        # a) Excel‐serial branch (for floats/ints)
        ser_num = pd.to_numeric(ser, errors='coerce')
        dt = pd.to_datetime(
            ser_num,
            unit='D',
            origin='1899-12-30',
            errors='coerce'
        )

        # b) String‐date fallback
        mask = dt.isna() & ser.notna()
        if mask.any():
            dt.loc[mask] = pd.to_datetime(
                ser[mask],
                dayfirst=True,
                errors='coerce'
            )

        tmp[col] = dt
        # debug print
        total = ser.notna().sum()
        good  = dt.notna().sum()
        print(f"  {col}: parsed {good}/{total} values into dates")

    df_list.append(tmp)

# 4) Concatenate end‐to‐end
df_start = pd.concat(df_list, ignore_index=True)
print("Final shape:", df_start.shape)


#df.iloc[46847:46857]
#df.tail(1300)
df_start.shape
#df_start.iloc[3000:3050]
#df_start

Processing file: Aida_Export_TESTin_0_1000.xlsx
  Incorporation year: parsed 998/998 values into dates
  Last accounting closing date: parsed 1000/1000 values into dates
Processing file: Aida_Export_TESTout_100001_101000.xlsx
  Incorporation year: parsed 1000/1000 values into dates
  Last accounting closing date: parsed 1000/1000 values into dates
Final shape: (3273, 16)


(3273, 16)

In [37]:
#@title Events Manipulation

# 2) Build your 'master' enterprises (one row per tax code)
master = (
    df_start[df_start['Tax code number'].notna()]
      .drop_duplicates(subset='Tax code number', keep='first')
)

# 3) Prepare the events table
events = (
    df_start[['Tax code number',
        'Procedure/cessazione',
        'Date of open procedure/cessazione',
        'Date of closure procedure']]
    .copy()
)
# fill down the tax‐code so every event row has its enterprise key
events['Tax code number'] = events['Tax code number'].ffill()

# keep only real events
events = events[events['Procedure/cessazione'].notna()].rename(columns={
    'Procedure/cessazione':        'Procedure',
    'Date of open procedure/cessazione': 'open_date',
    'Date of closure procedure':   'close_date'
})

# parse dates
events['open_date']  = pd.to_datetime(events['open_date'],  dayfirst=True, errors='coerce')
events['close_date'] = pd.to_datetime(events['close_date'], dayfirst=True, errors='coerce')

# 4) Sort & number each event per enterprise
events = (events
          .sort_values(['Tax code number', 'open_date'], ascending=[True, False]))
events['event_idx'] = events.groupby('Tax code number').cumcount()
events['event_idx'] = -events['event_idx']

# 5) Pivot to wide with unstack
df_e = events.set_index(['Tax code number','event_idx'])[['Procedure','open_date','close_date']]
df_un = df_e.unstack('event_idx')  # shape: index=tax codes, columns=(field, idx)
#5.1 order of tuples
field_order = ['Procedure','open_date','close_date']
idx_order   = sorted(df_un.columns.levels[1], reverse=True)

ordered_tuples = [
    (field, idx)
    for field in field_order
    for idx   in idx_order
    if (field, idx) in df_un.columns
]

df_un = df_un.reindex(columns=pd.MultiIndex.from_tuples(ordered_tuples))
# 6) Flatten the MultiIndex columns
df_un.columns = [
    (f"Event {i}"                 if field=='Procedure' else
     f"Date of open Event {i}"   if field=='open_date' else
     f"Date of closure Event {i}")
    for field, i in df_un.columns
]
df_un = df_un.reset_index()  # bring back Tax code number as a column

# 7) Merge back onto master (preserves your enterprise order)
final_df = (master
            .merge(df_un, on='Tax code number', how='left', sort=False)
            .reset_index(drop=True)
           )

#print(f"Enterprises: {len(master)}, rows in final_df: {len(final_df)}")
#final_df.head()

final_df = final_df.drop(columns=[
    'Procedure/cessazione',
    'Date of open procedure/cessazione',
    'Date of closure procedure'
])

In [38]:
#@title Appending
# 1) Treat only "n.a." as missing when reading
read_kwargs = dict(
    sheet_name="Results",
    index_col=None,
    na_values=["n.a."],
    keep_default_na=True
)

# 2) Read & stack all the new data end-to-end
df_list = []
for fn in test_files:
    tmp = pd.read_excel(path_data + fn, **read_kwargs)
    tmp['Tax code number'] = tmp['Tax code number'].astype('Int64')
    df_list.append(tmp)

In [39]:
#@title Balance sheet MANIPULATION - stacking and Fix Duplicate Column Names before mergingh

import re

# 1) Stack all new files into one DataFrame
all_new = pd.concat(df_list, ignore_index=True)


# Function to extract base name (without year) from column name
def get_base_name(col_name):
    """Extract the base variable name without the year, handling .1 .2 suffixes"""
    # First, remove any .1, .2, etc. suffix if present
    suffix_pattern = re.compile(r'\.\d+$')
    col_name_cleaned = suffix_pattern.sub('', col_name)

    # Now look for year at the end (after potential newlines)
    year_pattern = re.compile(r'(20\d{2})$', re.MULTILINE)
    if year_pattern.search(col_name_cleaned):
        # Remove the year to get base name
        base = year_pattern.sub('', col_name_cleaned).strip()
        return base
    return None

# Process all_new dataframe to add group prefixes
print("Processing all_new dataframe to fix duplicate column names...")
print(f"Original shape: {all_new.shape}")

# Get all columns
columns = list(all_new.columns)
new_columns = []
group_counter = 1
seen_groups = {}  # Track which base names we've seen and their group numbers
current_base = None
current_group = None

# Process columns in order
for i, col in enumerate(columns):
    base_name = get_base_name(col)

    if base_name is None:
        # Not a year column, keep as is
        new_columns.append(col)
    else:
        # Check if this is a new group
        if base_name != current_base:
            # New group detected
            if base_name in seen_groups:
                # We've seen this base name before, increment group number
                current_group = max(seen_groups[base_name]) + 1
                seen_groups[base_name].append(current_group)
            else:
                # First time seeing this base name
                current_group = group_counter
                seen_groups[base_name] = [current_group]
                group_counter += 1

            current_base = base_name

        # Add prefix to column name
        new_col_name = f"{current_group:04d}_{col}"
        new_columns.append(new_col_name)

# Apply new column names
all_new.columns = new_columns

print(f"\nTotal groups created: {group_counter - 1}")
print(f"Columns renamed: {len([old for old, new in zip(columns, new_columns) if old != new])}")

# Show examples of renamed columns
print("\nExamples of renamed columns:")
year_pattern = re.compile(r'(20\d{2})$', re.MULTILINE)
renamed_examples = [(old, new) for old, new in zip(columns, new_columns)
                    if old != new and year_pattern.search(old)][:10]

for old, new in renamed_examples:
    # Show in readable format
    old_display = old.replace('\n', '\\n')
    new_display = new.replace('\n', '\\n')
    print(f"  {old_display} -> {new_display}")

# Verify no duplicates remain
duplicate_cols = all_new.columns[all_new.columns.duplicated()].tolist()
if duplicate_cols:
    print(f"\n⚠️ Warning: Still have {len(duplicate_cols)} duplicate columns!")
    print(f"Duplicates: {duplicate_cols[:5]}")
else:
    print("\n✅ Success: No duplicate columns remaining!")

# Show column name patterns
print("\nColumn name patterns (first few groups):")
for base_name, groups in list(seen_groups.items())[:5]:
    base_display = base_name.split('\n')[0][:50]  # First line, max 50 chars
    print(f"  '{base_display}...' appears in groups: {groups}")

# Test the function
test_cases = [
    "Additions in progress and advances\nth EUR\n2023",
    "Additions in progress and advances\nth EUR\n2023.1",
    "Additions in progress and advances\nth EUR\n2023.2",
    "Company name",
    "Tax code number"
]

print("Testing improved get_base_name function:")
for test in test_cases:
    result = get_base_name(test)
    test_display = test.replace('\n', '\\n')
    print(f"  '{test_display}' -> {repr(result)}")

Processing all_new dataframe to fix duplicate column names...
Original shape: (2000, 4243)

Total groups created: 365
Columns renamed: 4240

Examples of renamed columns:
  Revenues from sales and services\nth EUR\n2023 -> 0001_Revenues from sales and services\nth EUR\n2023
  Revenues from sales and services\nth EUR\n2022 -> 0001_Revenues from sales and services\nth EUR\n2022
  Revenues from sales and services\nth EUR\n2021 -> 0001_Revenues from sales and services\nth EUR\n2021
  Revenues from sales and services\nth EUR\n2020 -> 0001_Revenues from sales and services\nth EUR\n2020
  Revenues from sales and services\nth EUR\n2019 -> 0001_Revenues from sales and services\nth EUR\n2019
  Revenues from sales and services\nth EUR\n2018 -> 0001_Revenues from sales and services\nth EUR\n2018
  Revenues from sales and services\nth EUR\n2017 -> 0001_Revenues from sales and services\nth EUR\n2017
  Revenues from sales and services\nth EUR\n2016 -> 0001_Revenues from sales and services\nth EUR\n201

In [40]:
#@title Merging

# 2) Ensure the key is the same type
all_new['Tax code number'] = all_new['Tax code number'].astype('Int64')

# 3) Perform a 1:1 left-join of your master with the new data,
df = final_df.merge(
    all_new,
    on='Tax code number',
    how='left',
    validate='one_to_one'
)
# Fix duplicate column names if they exist
if 'Company name_x' in df.columns and 'Company name_y' in df.columns:
    # Keep the one from final_df (left side) and drop the duplicate
    df['Company name'] = df['Company name_x']
    df = df.drop(columns=['Company name_x', 'Company name_y'])
    print("Fixed duplicate Company name columns")

print(df.shape)  # rows == final_df.rows; columns == union of both sets of variables


Fixed duplicate Company name columns
(2000, 4275)


In [41]:
#@title visualize big database

# Show *every* column
pd.set_option('display.max_columns', 1000)

# (Optionally widen your display so lines don’t wrap too crazily)
pd.set_option('display.width', 20)
pd.set_option('display.max_colwidth', 50)

# Now when you do…
#df

#print(final_df.iloc[:, :10])
#df.iloc[:30, :200]
#df.iloc[1000:1030, :200]

df.iloc[985:1015, :200]

Unnamed: 0_x  \
985          986.0   
986          987.0   
987          988.0   
988          989.0   
989          990.0   
990          991.0   
991          992.0   
992          993.0   
993          994.0   
994          995.0   
995          996.0   
996          997.0   
997          998.0   
998          999.0   
999         1000.0   
1000           1.0   
1001           2.0   
1002           3.0   
1003           4.0   
1004           5.0   
1005           6.0   
1006           7.0   
1007           8.0   
1008           9.0   
1009          10.0   
1010          11.0   
1011          12.0   
1012          13.0   
1013          14.0   
1014          15.0   

      Tax code number  \
985        2602271203   
986        2218090591   
987        1795590494   
988         708470158   
989        5054751002   
990        7447430724   
991       12949390152   
992        3090921200   
993        2361240241   
994       12643431005   
995        1039170376   
996        8256571004   
997        5073090879   
998        6758100017   
999        7773650960   
1000       1914330442   
1001      11336190019   
1002       2456700224   
1003      15763171004   
1004       1314010099   
1005      13218621004   
1006       1049120668   
1007       3533730127   
1008       2093260244   
1009       8142211211   
1010       1813120514   
1011       2818110302   
1012       9160710969   
1013       1976860591   
1014       3128400987   

      Registered office address - Postal code  \
985                                   40136.0   
986                                    4016.0   
987                                   57121.0   
988                                   20836.0   
989                                     148.0   
990                                   75100.0   
991                                   20068.0   
992                                   40050.0   
993                                   36050.0   
994                                     141.0   
995                                   40010.0   
996                                     166.0   
997                                   95037.0   
998                                   10071.0   
999                                     142.0   
1000                                  63813.0   
1001                                  10129.0   
1002                                  38013.0   
1003                                    182.0   
1004                                  17019.0   
1005                                    154.0   
1006                                  67015.0   
1007                                  21052.0   
1008                                  36030.0   
1009                                  80047.0   
1010                                  52025.0   
1011                                  33010.0   
1012                                  20139.0   
1013                                   4100.0   
1014                                  25050.0   

      Registered office address - Longitude  \
985                               11.338145   
986                               13.024707   
987                               10.326035   
988                                9.237839   
989                               12.438959   
990                               16.419107   
991                                9.285357   
992                               11.349318   
993                               11.369066   
994                                     NaN   
995                               11.419135   
996                               12.361889   
997                               15.105442   
998                                7.703643   
999                                9.264736   
1000                              13.678190   
1001                               7.661959   
1002                                    NaN   
1003                              12.518586   
1004                               8.566941   
1005                              12.495

In [42]:
print(df.shape)

(2000, 4275)


In [43]:
#@title LIST MISSING VARIABLES

# 1) Count columns that are 100% missing
all_nan = df.columns[df.isna().all()]
print(f"Columns with all NaN: {len(all_nan)}")

# 2) Drop them
df.drop(columns=all_nan, inplace=True)

# 3) Show the list of dropped columns
print("Dropped columns:")
for col in all_nan:
    print(f" - {col}")


Columns with all NaN: 759
Dropped columns:
 - Date of closure Event -6
 - 0081_Amounts due for advance taxation
th EUR
2023
 - 0081_Amounts due for advance taxation
th EUR
2022
 - 0081_Amounts due for advance taxation
th EUR
2021
 - 0081_Amounts due for advance taxation
th EUR
2020
 - 0081_Amounts due for advance taxation
th EUR
2019
 - 0081_Amounts due for advance taxation
th EUR
2018
 - 0081_Amounts due for advance taxation
th EUR
2017
 - 0081_Amounts due for advance taxation
th EUR
2016
 - 0081_Amounts due for advance taxation
th EUR
2015
 - 0081_Amounts due for advance taxation
th EUR
2014
 - 0109_GROUP consolidation reserve
th EUR
2023
 - 0109_GROUP consolidation reserve
th EUR
2022
 - 0109_GROUP consolidation reserve
th EUR
2021
 - 0109_GROUP consolidation reserve
th EUR
2020
 - 0109_GROUP consolidation reserve
th EUR
2019
 - 0109_GROUP consolidation reserve
th EUR
2018
 - 0109_GROUP consolidation reserve
th EUR
2017
 - 0109_GROUP consolidation reserve
th EUR
2016
 - 0109_GROUP c

In [44]:
#@title RANK OF MISSING in NON-MISSING VARIABLES

# 4) Compute missing counts for the rest, sort descending
missing_counts = df.isna().sum().sort_values(ascending=False)

# Ensure pandas will print all rows
pd.set_option('display.max_rows', None)

print("\nMissing‐value counts for remaining columns (desc):")
print(missing_counts)



Missing‐value counts for remaining columns (desc):
0293_Total cash and cash equivalents at beginning of the year\nth EUR\n2015                                                                1999
0294_of which restricted\nth EUR\n2022                                                                                                     1999
0294_of which restricted\nth EUR\n2017                                                                                                     1999
0289_Net effect on cash and cash equivalents\nth EUR\n2019                                                                                 1999
0289_Net effect on cash and cash equivalents\nth EUR\n2020                                                                                 1999
0288_Increase/(Decrease) in cash and cash equivalents (A + B + C)\nth EUR\n2015                                                            1999
0289_Net effect on cash and cash equivalents\nth EUR\n2022                          

In [45]:
#@title SAVE PROCESSED DATASET (Wide Format)
import pickle

# Save the processed wide format dataset
save_path = path_data + 'processed_df_wide.pkl'
df.to_pickle(save_path)
print(f"✅ Saved processed dataset to: {save_path}")
print(f"Shape: {df.shape}, Size: {df.memory_usage(deep=True).sum() / 1024**2:.1f} MB")

✅ Saved processed dataset to: /content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/DATA/model_test/processed_df_wide.pkl
Shape: (2000, 3516), Size: 60.2 MB


### (#) open dataset created

In [ ]:
#@title LOAD PROCESSED DATASET (Wide Format)
import pickle
import pandas as pd
import re

# Load the pre-processed dataset
load_path = path_data + 'processed_df_wide.pkl'

try:
    df = pd.read_pickle(load_path)
    print(f"✅ Loaded processed dataset from: {load_path}")
    print(f"Shape: {df.shape}")
    print(f"Columns with 'date'/'year': {len([c for c in df.columns if re.search(r'(year|date)$', c, re.IGNORECASE)])}")

    # Quick validation that dates are still datetime objects
    date_cols = [c for c in df.columns if re.search(r'(year|date)$', c, re.IGNORECASE)]
    if date_cols:
        sample_col = date_cols[0]
        print(f"Date dtype check - {sample_col}: {df[sample_col].dtype}")

    # Check event columns
    event_cols = [c for c in df.columns if c.startswith('Event ')]
    print(f"Event columns found: {len(event_cols)}")

except FileNotFoundError:
    print("❌ Processed file not found. Run the full import process first.")
except Exception as e:
    print(f"❌ Error loading processed file: {e}")

✅ Loaded processed dataset from: /content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/DATA/model_test/processed_df_wide.pkl
Shape: (2000, 3517)
Columns with 'date'/'year': 2
Date dtype check - Incorporation year: datetime64[ns]
Event columns found: 7


### stats

---



In [ ]:
#@title missing variables
# 1) Row‐count sanity: you should still have exactly one row per tax code
n_rows = df.shape[0]
n_unique_codes = df['Tax code number'].nunique()
print(f"Rows: {n_rows}, Unique Tax codes: {n_unique_codes}")

# 2) Check for any duplicate tax codes (should be zero)
dups = df['Tax code number'].duplicated().sum()
print(f"Duplicate keys: {dups}")

# 3) Overall missing‐value summary
missing_per_col = df.isna().sum().sort_values(ascending=False)
print("Top 10 columns by # missing values:")
print(missing_per_col.iloc[30:90])

Rows: 2000, Unique Tax codes: 2000
Duplicate keys: 0
Top 10 columns by # missing values:
Tax code number                            0
Legal status                               0
Company category                           0
Registered office address - Postal code    0
dtype: int64


In [ ]:
#@title only missing variables

# 1) Compute total missing per column
missing = df.isna().sum()

# 2) Filter to only those with at least one missing
missing = missing[missing > 0]

# 3) Sort descending (largest gaps first)
missing = missing.sort_values(ascending=False)

# 4) Make sure pandas will print every row
pd.set_option('display.max_rows', None)

# 5) Now display
print(missing)


Total cash and cash equivalents at year end\n2018    2000
Total cash and cash equivalents at year end\n2020    2000
Total cash and cash equivalents at year end\n2019    2000
Total cash and cash equivalents at year end\n2021    2000
Total cash and cash equivalents at year end\n2022    2000
Total cash and cash equivalents at year end\n2023    2000
Date of closure Event -6                             2000
Total cash and cash equivalents at year end\n2017    2000
Total cash and cash equivalents at year end\n2014    2000
Total cash and cash equivalents at year end\n2016    2000
Total cash and cash equivalents at year end\n2015    2000
Date of closure Event -5                             1998
Event -6                                             1998
Date of open Event -6                                1998
Date of closure Event -4                             1997
Event -5                                             1995
Date of open Event -5                                1995
Date of closur

In [ ]:
#@title visualize big part of database

from google.colab import data_table

# Turn on Colab’s interactive DataFrame display
data_table.enable_dataframe_formatter()

# Now this will show you an interactive, scrollable table
# (you can still slice it to a column range if you like)
#display(df)

# — or to only see columns 20 through 39 —
display(df.iloc[:, 170:200])


In [ ]:
#@title CHECK COLLINEARITY, MISSINGNESS & MORE (Corrected)

from statsmodels.stats.outliers_influence import variance_inflation_factor

# 1) Missing‐value summary on df
miss_pct = df.isnull().mean().sort_values(ascending=False)
print(">> Top 10 columns by percent missing:")
print(miss_pct.head(100).apply(lambda x: f"{x:.1%}"))
print("\n>> Columns with 100% missing:")
print(miss_pct[miss_pct == 1.0].index.tolist())

# 2) Data‐type & cardinality overview (drop the list‐column if present)
if 'ALL_events' in df.columns:
    basic = df.drop(columns=['ALL_events'])
else:
    basic = df.copy()

nunique = basic.nunique(dropna=False)
dtype_df = pd.DataFrame({
    'dtype':    basic.dtypes.astype(str),
    'n_unique': nunique
})
print("\n>> Data types and unique counts (sorted by dtype):")
print(dtype_df.sort_values('n_unique').head(10))

# 3) Correlation on numeric features (excluding fully‐missing columns)
#    Select columns with <100% missing, then pick numeric
valid_cols = miss_pct[miss_pct < 1.0].index
num = df[valid_cols].select_dtypes(include=[np.number])

corr = num.corr().abs()
high_corr = (
    corr.where(np.tril(np.ones(corr.shape), k=-1).astype(bool))
        .stack()
        .loc[lambda s: s > 0.90]
        .sort_values(ascending=False)
)
print(f"\n>> Highly correlated pairs (>|0.90|) [count={len(high_corr)}]:")
print(high_corr.head(10))

# 4) Variance Inflation Factor (VIF)
num_for_vif = num.fillna(0).astype(float)
vif_df = pd.DataFrame({
    'variable': num_for_vif.columns,
    'VIF': [
        variance_inflation_factor(num_for_vif.values, i)
        for i in range(num_for_vif.shape[1])
    ]
}).sort_values('VIF', ascending=False)
print("\n>> Top 10 variables by VIF:")
print(vif_df.head(10))

# 5) Distribution diagnostics for numeric columns
print("\n>> Skewness of numeric features:")
print(num.skew().sort_values(ascending=False).head(10))

outliers = ((num - num.mean()).abs() > 3 * num.std()) \
            .sum() \
            .sort_values(ascending=False)
print("\n>> Count of outliers (>|3σ|) per numeric feature:")
print(outliers.head(10))


### TEST COLAB

---



In [46]:
#@title Bankruptcy dummy
import pandas as pd
import numpy as np

# Create bankruptcy dummy and date variables
df['Bankruptcy_dummy'] = 0
df['Bankruptcy_dummy_date'] = pd.NaT

# Find all event columns
event_cols = [c for c in df.columns if c.startswith('Event ') and not c.startswith('Date of')]

print(f"Checking {len(event_cols)} event columns for bankruptcy...")

# For each row, check if any event contains "Bankruptcy"
bankruptcy_count = 0

for idx, row in df.iterrows():
    for event_col in event_cols:
        event_value = row[event_col]

        # Check if this event is exactly "Bankruptcy" (case sensitive)
        if pd.notna(event_value) and event_value == 'Bankruptcy':
            # Set the dummy to 1
            df.loc[idx, 'Bankruptcy_dummy'] = 1

            # Extract the event number from column name (e.g., "Event -2" -> "-2")
            event_num = event_col.replace('Event ', '')

            # Find the corresponding date column
            date_col = f'Date of open Event {event_num}'

            # If the date column exists and has a value, store it
            if date_col in df.columns and pd.notna(row[date_col]):
                df.loc[idx, 'Bankruptcy_dummy_date'] = pd.to_datetime(row[date_col])
                bankruptcy_count += 1
                break  # Stop after finding the first bankruptcy event

# Convert date column to datetime type
df['Bankruptcy_dummy_date'] = pd.to_datetime(df['Bankruptcy_dummy_date'])

# Display summary
print(f"\nTotal enterprises with Bankruptcy event: {df['Bankruptcy_dummy'].sum()}")
print(f"Enterprises with valid bankruptcy dates: {bankruptcy_count}")

# Show distribution
print("\nBankruptcy_dummy distribution:")
print(df['Bankruptcy_dummy'].value_counts())

# Show sample of enterprises with bankruptcy
bankrupt_sample = df[df['Bankruptcy_dummy'] == 1][['Tax code number', 'Company name', 'Bankruptcy_dummy', 'Bankruptcy_dummy_date']].head(10)
print("\nSample of enterprises with bankruptcy:")
display(bankrupt_sample)

Checking 7 event columns for bankruptcy...

Total enterprises with Bankruptcy event: 301
Enterprises with valid bankruptcy dates: 300

Bankruptcy_dummy distribution:
Bankruptcy_dummy
0    1699
1     301
Name: count, dtype: int64

Sample of enterprises with bankruptcy:


Tax code number  \
8          647460286   
36        4261290821   
53        2229420415   
67        1614500799   
71        3074840160   
76         301260725   
94        3725790137   
97        1697130464   
100       6850091007   
102      13116741003   

                                          Company name  \
8                                         VIMET S.P.A.   
36                         FENICE DISTRIBUZIONE S.R.L.   
53                                   BENELLI Q. J. SRL   
67   LA NUOVA NAVE SOCIETA' A RESPONSABILITA' LIMIT...   
71                              ONGIS METAL FER S.P.A.   
76   ALBERGO PETROLI SOCIETA' A RESPONSABILITA' LIM...   
94                       NUOVA REX SUPERMERCATI S.R.L.   
97                     PERINI NAVI SOCIETA' PER AZIONI   
100            JENNIFER PETROLI S.R.L. IN LIQUIDAZIONE   
102                                     CARFUEL S.R.L.   

     Bankruptcy_dummy  \
8                   1   
36                  1   
53                  1   
67                  1   
71                  1   
76                  1   
94                  1   
97                  1   
100                 1   
102                 1   

    Bankruptcy_dummy_date  
8              2017-03-03  
36             2017-05-15  
53             2016-07-12  
67             2021-10-12  
71             2018-03-16  
76             2021-11-08  
94             2021-07-22  
97             2021-01-29  
100            2017-01-10  
102            2018-05-08

In [53]:
#@title Reshape Long
import pandas as pd
import numpy as np
import re
import gc

# Starting from `df` which has Bankruptcy_dummy and Bankruptcy_dummy_date

# 1. First, identify columns with years
year_pattern = re.compile(r'(20\d{2})(?:\.\d+)?$', re.MULTILINE)  # Matches year with optional .1, .2 suffix
wide_cols = [col for col in df.columns if year_pattern.search(col)]
id_cols = [c for c in df.columns if c not in wide_cols]

print(f"Found {len(wide_cols)} columns with years")
print(f"Number of ID columns: {len(id_cols)}")
print(f"Total enterprises: {len(df)}")

# 2. Create a function to extract variable name and year
def parse_column_name(col_name):
    """Extract clean variable name and year from column"""
    year_match = year_pattern.search(col_name)
    if year_match:
        year = int(year_match.group(1))
        # Get variable name (first line before \n)
        var_name = col_name.split('\n')[0].strip()
        return var_name, year
    return None, None

# 3. Get unique years and variables
years = set()
variables = set()
col_mapping = {}  # Maps (variable, year) to original column name

for col in wide_cols:
    var_name, year = parse_column_name(col)
    if var_name and year:
        years.add(year)
        variables.add(var_name)
        col_mapping[(var_name, year)] = col

years = sorted(years)
variables = sorted(variables)

print(f"\nYears found: {min(years)} to {max(years)} (Total: {len(years)} years)")
print(f"Number of unique variables: {len(variables)}")
print(f"Expected max rows (if no bankruptcy): {len(df) * len(years):,}")

# 4. Process in chunks to save memory
chunk_size = 100  # Process 100 enterprises at a time
long_chunks = []
total_rows_created = 0
enterprises_truncated = 0

print("\nProcessing in chunks to save memory...")

for chunk_start in range(0, len(df), chunk_size):
    chunk_end = min(chunk_start + chunk_size, len(df))

    # Get chunk of enterprises
    df_chunk = df.iloc[chunk_start:chunk_end]

    # Create list to store long format data for this chunk
    chunk_data = []

    for _, row in df_chunk.iterrows():
        tax_code = row['Tax code number']

        # Get bankruptcy year if exists
        bankruptcy_year = None
        if row['Bankruptcy_dummy'] == 1 and pd.notna(row['Bankruptcy_dummy_date']):
            bankruptcy_year = row['Bankruptcy_dummy_date'].year
            enterprises_truncated += 1

        # For each year
        rows_for_enterprise = 0
        for year in years:
            # Skip years after bankruptcy
            if bankruptcy_year and year > bankruptcy_year:
                continue

            # Create row for this enterprise-year
            long_row = {}

            # Add ID columns (including Bankruptcy_dummy and Bankruptcy_dummy_date)
            for id_col in id_cols:
                long_row[id_col] = row[id_col]

            # Add year
            long_row['Year'] = year

            # Add variable values for this year
            for var_name in variables:
                col_key = (var_name, year)
                if col_key in col_mapping:
                    orig_col = col_mapping[col_key]
                    if orig_col in row.index:
                        long_row[var_name] = row[orig_col]
                    else:
                        long_row[var_name] = np.nan
                else:
                    long_row[var_name] = np.nan

            chunk_data.append(long_row)
            rows_for_enterprise += 1
            total_rows_created += 1

    # Convert chunk to dataframe
    chunk_long = pd.DataFrame(chunk_data)
    long_chunks.append(chunk_long)

    # Progress update
    if (chunk_end % 500 == 0) or (chunk_end == len(df)):
        print(f"  Processed {chunk_end}/{len(df)} enterprises... Total rows created: {total_rows_created:,}")

    # Clean up memory
    del chunk_data
    gc.collect()

# 5. Combine all chunks
print("\nCombining chunks...")
long_df = pd.concat(long_chunks, ignore_index=True)

# Clean up
del long_chunks
gc.collect()

# 6. Add derived columns
print("\nAdding derived columns...")

# Create NameYear using the actual Company name column
if 'Company name' in long_df.columns:
    long_df['NameYear'] = long_df['Company name'].astype(str) + ' ' + long_df['Year'].astype(str)
    print("Using 'Company name' column for NameYear")
else:
    print("Warning: 'Company name' column not found!")

# Create KeyYear using Tax code number + Year
long_df['KeyYear'] = long_df['Tax code number'].astype(str) + '_' + long_df['Year'].astype(str)

# 7. Sort the data
long_df = long_df.sort_values(['Tax code number', 'Year']).reset_index(drop=True)

# 8. Display summary
print(f"\nFinal shape: {long_df.shape}")
print(f"Memory usage: {long_df.memory_usage(deep=True).sum() / 1024**3:.2f} GB")
print(f"Unique enterprises: {long_df['Tax code number'].nunique()}")
print(f"Years covered: {long_df['Year'].min()} to {long_df['Year'].max()}")
print(f"Enterprises truncated due to bankruptcy: {enterprises_truncated}")

# Check observation count per enterprise
obs_per_enterprise = long_df.groupby('Tax code number').size()
print(f"\nObservations per enterprise:")
print(obs_per_enterprise.value_counts().sort_index())

# 9. Save to file
print("\nSaving to pickle file...")
long_df.to_pickle(path_data + 'long_format_data.pkl')
print("Saved successfully!")

# 10. Show sample
print("\nSample of reshaped data (first 20 rows):")
display(long_df.head(20))

# Show a company with bankruptcy
bankrupt_companies = long_df[long_df['Bankruptcy_dummy'] == 1]['Tax code number'].unique()
if len(bankrupt_companies) > 0:
    sample_bankrupt = bankrupt_companies[0]
    print(f"\nSample bankrupt company {sample_bankrupt}:")
    display(long_df[long_df['Tax code number'] == sample_bankrupt])

# Show columns
print("\nColumns in long format (first 50):")
for i, col in enumerate(long_df.columns[:50]):
    print(f"  {i+1}. {col}")

Found 3482 columns with years
Number of ID columns: 36
Total enterprises: 2000

Years found: 2014 to 2023 (Total: 10 years)
Number of unique variables: 356
Expected max rows (if no bankruptcy): 20,000

Processing in chunks to save memory...
  Processed 500/2000 enterprises... Total rows created: 4,545
  Processed 1000/2000 enterprises... Total rows created: 8,761
  Processed 1500/2000 enterprises... Total rows created: 13,761
  Processed 2000/2000 enterprises... Total rows created: 18,761

Combining chunks...

Adding derived columns...
Using 'Company name' column for NameYear

Final shape: (18761, 395)
Memory usage: 0.07 GB
Unique enterprises: 1995
Years covered: 2014 to 2023
Enterprises truncated due to bankruptcy: 300

Observations per enterprise:
1        2
3        9
4       49
5       64
6       67
7       38
8       47
9       18
10    1701
Name: count, dtype: int64

Saving to pickle file...
Saved successfully!

Sample of reshaped data (first 20 rows):


Unnamed: 0_x  \
0          925.0   
1          925.0   
2          925.0   
3          925.0   
4          925.0   
5          925.0   
6          925.0   
7          925.0   
8          925.0   
9          925.0   
10         375.0   
11         375.0   
12         375.0   
13         375.0   
14         375.0   
15         375.0   
16         375.0   
17         375.0   
18         375.0   
19         375.0   

    Tax code number  \
0          27110881   
1          27110881   
2          27110881   
3          27110881   
4          27110881   
5          27110881   
6          27110881   
7          27110881   
8          27110881   
9          27110881   
10         40810384   
11         40810384   
12         40810384   
13         40810384   
14         40810384   
15         40810384   
16         40810384   
17         40810384   
18         40810384   
19         40810384   

    Registered office address - Postal code  \
0                                   97100.0   
1                                   97100.0   
2                                   97100.0   
3                                   97100.0   
4                                   97100.0   
5                                   97100.0   
6                                   97100.0   
7                                   97100.0   
8                                   97100.0   
9                                   97100.0   
10                                  44124.0   
11                                  44124.0   
12                                  44124.0   
13                                  44124.0   
14                                  44124.0   
15                                  44124.0   
16                                  44124.0   
17                                  44124.0   
18                                  44124.0   
19                                  44124.0   

    Registered office address - Longitude  \
0                               14.744959   
1                               14.744959   
2                               14.744959   
3                               14.744959   
4                               14.744959   
5                               14.744959   
6                               14.744959   
7                               14.744959   
8                               14.744959   
9                               14.744959   
10                              11.620403   
11                              11.620403   
12                              11.620403   
13                              11.620403   
14                              11.620403   
15                              11.620403   
16                              11.620403   
17                              11.620403   
18                              11.620403   
19                              11.620403   

    Registered office address - Latitude  \
0                              36.925594   
1                              36.925594   
2                              36.925594   
3                              36.925594   
4                              36.925594   
5                              36.925594   
6                              36.925594   
7                              36.925594   
8                              36.925594   
9                              36.925594   
10                             44.837851   
11                             44.837851   
12                             44.837851   
13                             44.837851   
14                             44.837851   
15                             44.837851   
16                             44.837851   
17                             44.837851   
18                             44.837851   
19                             44.837851   

    Trading address - Postal code  \
0                         97100.0   
1                         97100.0   
2                         97100.0   
3                         97100.0   
4                         97100.0   
5                 


Sample bankrupt company 124550401:


Unnamed: 0_x  \
320         663.0   
321         663.0   
322         663.0   
323         663.0   

     Tax code number  \
320        124550401   
321        124550401   
322        124550401   
323        124550401   

     Registered office address - Postal code  \
320                                  47122.0   
321                                  47122.0   
322                                  47122.0   
323                                  47122.0   

     Registered office address - Longitude  \
320                              12.063292   
321                              12.063292   
322                              12.063292   
323                              12.063292   

     Registered office address - Latitude  \
320                             44.221958   
321                             44.221958   
322                             44.221958   
323                             44.221958   

     Trading address - Postal code  \
320                            NaN   
321                            NaN   
322                            NaN   
323                            NaN   

               Legal status  \
320  Dissolved (bankruptcy)   
321  Dissolved (bankruptcy)   
322  Dissolved (bankruptcy)   
323  Dissolved (bankruptcy)   

                    Legal form  \
320  Joint stock company - SPA   
321  Joint stock company - SPA   
322  Joint stock company - SPA   
323  Joint stock company - SPA   

    Company category  \
320  Limited company   
321  Limited company   
322  Limited company   
323  Limited company   

    Incorporation year  \
320         1965-10-12   
321         1965-10-12   
322         1965-10-12   
323         1965-10-12   

     No of available years  \
320                   10.0   
321                   10.0   
322                   10.0   
323                   10.0   

    Last accounting closing date  \
320                   2014-12-31   
321                   2014-12-31   
322                   2014-12-31   
323                   2014-12-31   

                                 Event 0  \
320  Conclusion of bankruptcy procedures   
321  Conclusion of bankruptcy procedures   
322  Conclusion of bankruptcy procedures   
323  Conclusion of bankruptcy procedures   

       Event -1  \
320  Bankruptcy   
321  Bankruptcy   
322  Bankruptcy   
323  Bankruptcy   

    Event -2  \
320      NaN   
321      NaN   
322      NaN   
323      NaN   

    Event -3  \
320      NaN   
321      NaN   
322      NaN   
323      NaN   

    Event -4  \
320      NaN   
321      NaN   
322      NaN   
323      NaN   

    Event -5  \
320      NaN   
321      NaN   
322      NaN   
323      NaN   

    Event -6  \
320      NaN   
321      NaN   
322      NaN   
323      NaN   

    Date of open Event 0  \
320           2021-10-13   
321           2021-10-13   
322           2021-10-13   
323           2021-10-13   

    Date of open Event -1  \
320            2017-01-26   
321            2017-01-26   
322            2017-01-26   
323            2017-01-26   

    Date of open Event -2  \
320                   NaT   
321                   NaT   
322                   NaT   
323                   NaT   

    Date of open Event -3  \
320                   NaT   
321                   NaT   
322                   NaT   
323                   NaT   

    Date of open Event -4  \
320                   NaT   
321                   NaT   
322                   NaT   
323                   NaT   

    Date of open Event -5  \
320                   NaT   
321                   NaT   
322                   NaT   
323                   NaT   

    Date of open Event -6  \
320                   NaT   
321                   NaT   
322                   NaT   
323                   NaT   

    Date of closure Event 0  \
320                     NaT   
321                     NaT   
322                     NaT   
323                     NaT   

    Date of closure Event -1  \
320                      NaT   
321                


Columns in long format (first 50):
  1. Unnamed: 0_x
  2. Tax code number
  3. Registered office address - Postal code
  4. Registered office address - Longitude
  5. Registered office address - Latitude
  6. Trading address - Postal code
  7. Legal status
  8. Legal form
  9. Company category
  10. Incorporation year
  11. No of available years
  12. Last accounting closing date
  13. Event 0
  14. Event -1
  15. Event -2
  16. Event -3
  17. Event -4
  18. Event -5
  19. Event -6
  20. Date of open Event 0
  21. Date of open Event -1
  22. Date of open Event -2
  23. Date of open Event -3
  24. Date of open Event -4
  25. Date of open Event -5
  26. Date of open Event -6
  27. Date of closure Event 0
  28. Date of closure Event -1
  29. Date of closure Event -2
  30. Date of closure Event -3
  31. Date of closure Event -4
  32. Date of closure Event -5
  33. Unnamed: 0_y
  34. Company name
  35. Bankruptcy_dummy
  36. Bankruptcy_dummy_date
  37. Year
  38. 0001_Revenues from sales a

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_25['0008_Return on sales (ROS)'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_25, x='Year', y='0008_Return on sales (ROS)', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `x` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_26['0010_Return on equity (ROE)'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_26, x='Year', y='0010_Return on equity (ROE)', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `x` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_27['0011_Debt/equity ratio'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_27, x='Year', y='0011_Debt/equity ratio', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [52]:
#long_df.head()
#df.head()
long_df.iloc[985:1015, 200:400]
#df.iloc[985:1015, :200]

0292_Bank and Post office deposits\nth EUR\n2015.1  \
985                                                 NaN    
986                                                 NaN    
987                                                 NaN    
988                                                 NaN    
989                                                 NaN    
990                                                 NaN    
991                                                 NaN    
992                                                 NaN    
993                                                 NaN    
994                                                 NaN    
995                                                 NaN    
996                                                 NaN    
997                                                 NaN    
998                                                 NaN    
999                                                 NaN    
1000                                                NaN    
1001                                                NaN    
1002                                                NaN    
1003                                                NaN    
1004                                                NaN    
1005                                                NaN    
1006                                                NaN    
1007                                                NaN    
1008                                                NaN    
1009                                                NaN    
1010                                                NaN    
1011                                                NaN    
1012                                                NaN    
1013                                                NaN    
1014                                                NaN    

      0293_Cheques\nth EUR\n2023.1  \
985                            NaN   
986                            NaN   
987                            NaN   
988                            NaN   
989                            NaN   
990                            NaN   
991                            NaN   
992                            NaN   
993                            NaN   
994                            NaN   
995                            NaN   
996                            NaN   
997                            NaN   
998                            NaN   
999                            NaN   
1000                           NaN   
1001                           NaN   
1002                           NaN   
1003                           NaN   
1004                           NaN   
1005                           NaN   
1006                           NaN   
1007                           NaN   
1008                           NaN   
1009                           NaN   
1010                           NaN   
1011                           NaN   
1012                           NaN   
1013                           NaN   
1014                           NaN   

      0293_Cheques\nth EUR\n2022.1  \
985                            NaN   
986                            NaN   
987                            NaN   
988                            NaN   
989                            NaN   
990                            NaN   
991                            NaN   
992                            NaN   
993                            NaN   
994                            NaN   
995                            NaN   
996                            NaN   
997                            NaN   
998                            NaN   
999                            NaN   
1000                           NaN   
1001                           NaN   
1002                           NaN   
1003                           NaN   
1004                           NaN   
1005                           NaN   
1006                           NaN   
1007                           NaN   
1008                           NaN   
1009            

In [54]:
#@title SAVE LONG FORMAT DATASET
# This is already in your reshape code, but here's a standalone version
if 'long_df' in locals():
    save_path_long = path_data + 'long_format_data.pkl'
    long_df.to_pickle(save_path_long)
    print(f"✅ Saved long format dataset to: {save_path_long}")
    print(f"Shape: {long_df.shape}, Size: {long_df.memory_usage(deep=True).sum() / 1024**2:.1f} MB")
else:
    print("❌ long_df not found. Run the Reshape Long cell first.")

✅ Saved long format dataset to: /content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/DATA/model_test/long_format_data.pkl
Shape: (18761, 395), Size: 75.1 MB


In [ ]:
#@title LOAD LONG FORMAT DATASET
import pickle
import pandas as pd

load_path_long = path_data + 'long_format_data.pkl'

try:
    long_df = pd.read_pickle(load_path_long)
    print(f"✅ Loaded long format dataset from: {load_path_long}")
    print(f"Shape: {long_df.shape}")
    print(f"Unique enterprises: {long_df['Tax code number'].nunique()}")
    print(f"Years covered: {long_df['Year'].min()} to {long_df['Year'].max()}")

    # Check key variables
    if 'KeyYear' in long_df.columns:
        print("✅ KeyYear variable present")
    if 'NameYear' in long_df.columns:
        print("✅ NameYear variable present")

    # Show observation distribution
    obs_per_enterprise = long_df.groupby('Tax code number').size()
    print(f"\nObservations per enterprise distribution:")
    print(obs_per_enterprise.value_counts().sort_index().head())

except FileNotFoundError:
    print("❌ Long format file not found. Run the Reshape Long process first.")
except Exception as e:
    print(f"❌ Error loading long format file: {e}")

✅ Loaded long format dataset from: /content/drive/MyDrive/SETUP DEFINITIVO/Temporaneo, lezioni ML/AIDA/DATA/model_test/long_format_data.pkl
Shape: (18761, 569)
Unique enterprises: 1995
Years covered: 2014 to 2023
✅ KeyYear variable present

Observations per enterprise distribution:
1     2
3     9
4    49
5    64
6    67
Name: count, dtype: int64


In [66]:
import pandas as pd

from google.colab import data_table

sample = long_df.sample(min(30, len(long_df)), random_state=42)
data_table.DataTable(sample,
                     include_index=False,
                     max_columns=500,           # only this table
                     num_rows_per_page=25)
import pandas as pd
pd.set_option("display.max_columns", None)     # never truncate columns
pd.set_option("display.expand_frame_repr", False)
pd.set_option("display.max_colwidth", None)
display(sample)                                # full 395 × n view


Unnamed: 0_x  Tax code number  Registered office address - Postal code  Registered office address - Longitude  Registered office address - Latitude  Trading address - Postal code                     Legal status                                                      Legal form Company category Incorporation year  No of available years Last accounting closing date                                                                  Event 0                               Event -1                    Event -2                      Event -3 Event -4 Event -5 Event -6 Date of open Event 0 Date of open Event -1 Date of open Event -2 Date of open Event -3 Date of open Event -4 Date of open Event -5 Date of open Event -6 Date of closure Event 0 Date of closure Event -1 Date of closure Event -2 Date of closure Event -3 Date of closure Event -4 Date of closure Event -5  Unnamed: 0_y                                                                                                          Company name  Bankruptcy_dummy Bankruptcy_dummy_date  Year  0001_Revenues from sales and services  0002_EBITDA  0002_Revenues from sales and services  0003_Profit (loss)  0004_Total assets  0005_Total shareholder's funds  0006_Net financial position 0007_EBITDA/Vendite 0008_Return on sales (ROS)  0009_Return on asset (ROA) 0010_Return on equity (ROE) 0011_Debt/equity ratio 0012_Banks/turnover 0013_Debt/EBITDA ratio 0014_Total assets turnover (times)  0015_Number of employees  0016_TOTAL receivables due from shareholders  0017_Called share capital  0018_TOTAL FIXED ASSETS  0019_TOTAL INTANGIBLE FIXED ASSETS  0020_Start-up and expansion costs  0021_Research and dev. exp.  0022_Ind. patents and intellect. property rights  0023_Concessions, licenses, trademarks and similar rights  0024_Goodwill/Consolidation Difference  0025_including: Goodwill  0026_Additions in progress and advances  0027_Additions in progress and advances  0027_Others  0028_(Amortization provision)  0029_TOTAL TANGIBLE FIXED ASSETS  0030_including: leased tangible assets  0031_Land and buildings  0032_Plant and machinery  0033_Indust. and commercial equipment  0034_Other assets  0035_(Depreciation provision)  0036_TOTAL FINANCIAL FIXED ASSETS  0037_including: short term  0038_Total equity investments  0039_Subsidiary companies  0040_Associated companies  0041_Parent companies  0042_Companies under parent companies control  0043_Other companies  0044_Total Receivables  0045_Receiv. due from subs. Comp.  0046_Receiv. due from subs. Comp.  0046_Receiv. due from subs. companies - beyond 12 months  0047_Receiv. due from assoc. companies  0048_Receiv. due from assoc. companies - beyond 12 months  0049_Receiv. due from parent comp. - beyond 12 months  0050_Due from comp. under parent companies control  0050_Receiv. due from parent comp. - beyond 12 months  0051_Due from comp. under parent companies control  0051_Due from comp. under parent companies control - beyond 12 months  0052_Due from comp. under parent companies control - beyond 12 months  0052_Receiv. due from other comp.  0053_Receiv. due from others - beyond 12 months  0054_FIN. RECEIV. WITHIN 12 MONTHS  0054_Receiv. due from others - beyond 12 months  0055_FINA. RECEIV. BEYOND 12 MONTHS  0056_Other securities  0057_Other securities  0057_Own shares  0058_Derivatives  0058_Own shares  0059_Derivatives  0059_Own shares: par value  0060_Own shares: par value  0060_TOTAL CURRENT ASSETS  0061_TOTAL INVENTORIES  0062_Raw and consumable materials  0063_Work in progress and semifinished products  0064_Contract work in progress  0065_Finished products and goods  0066_Advances  0067_Advances  0067_Tangible fixed assets to be sold  0068_TOTAL RECEIVABLES  0069_Trade accounts  0070_Trade accounts - beyond 12 months  0071_Receiv. due from subs. comp. - beyond 12 months  0072_Receiv. due from assoc. Comp.  0073_Receiv. due from assoc. Comp. - beyond 12 months  0074_Receiv. due from parent comp.  0075_Tax receivables  0076_Tax receiv. - beyond 12 months  0077

In [73]:
#@title  make_clean_bankruptcy_dataset.py

import re
import numpy as np
import pandas as pd

# ------------------------------------------------------------------
# 1. LOAD  – adjust the file names to your paths
# ------------------------------------------------------------------

last_df = long_df
OUTPUT_PATH = "last_df_clean.parquet"

# Preserve leading zeros in tax codes (important for joins)


# ------------------------------------------------------------------
# 2. PARSE DATE COLUMNS
# ------------------------------------------------------------------
date_cols = [c for c in last_df.columns
             if c.startswith("Date of open Event") or
                c.startswith("Date of closure Event")]

for col in date_cols + ["Bankruptcy_dummy_date"]:
    if col in last_df.columns:
        last_df[col] = pd.to_datetime(last_df[col], errors="coerce")

# ------------------------------------------------------------------
# 3. ALIGN EACH EVENT WITH THE CORRECT YEAR
# ------------------------------------------------------------------
event_cols = [c for c in last_df.columns if re.fullmatch(r"Event [\-\d]+", c)]

for ev in event_cols:
    open_col = f"Date of open {ev}"
    if open_col in last_df.columns:
        # keep the event only in the year in which it opened
        same_year = last_df[open_col].dt.year == last_df["Year"]
        last_df[ev] = last_df[ev].where(same_year)

# ------------------------------------------------------------------
# 4. FIRST BANKRUPTCY YEAR PER COMPANY
# ------------------------------------------------------------------
# “bankrupt” (EN) catches “Bankruptcy”, “Post-bankruptcy …” etc.
bankrupt_rows = last_df[event_cols].apply(
    lambda s: s.str.contains("bankrupt", case=False, na=False)).any(axis=1)

first_bankr_year = (
    last_df.loc[bankrupt_rows, ["Tax code number", "Year"]]
      .groupby("Tax code number")["Year"]
      .min()
)

# ------------------------------------------------------------------
# 5. TARGET = bankruptcy in NEXT YEAR
# ------------------------------------------------------------------
last_df["FirstBankrYear"] = last_df["Tax code number"].map(first_bankr_year)

# Drop the last observed year for each firm – no “next year” exists
last_year = last_df.groupby("Tax code number")["Year"].transform("max")
last_df = last_df[last_df["Year"] < last_year]

last_df["Target"] = (
    (last_df["FirstBankrYear"].notna()) &
    (last_df["Year"] + 1 == last_df["FirstBankrYear"])
).astype(int)

# ------------------------------------------------------------------
# 6. DROP HELPER / LEAKING COLUMNS
# ------------------------------------------------------------------
cols_to_drop = (
      ["FirstBankrYear", "Bankruptcy_dummy", "Bankruptcy_dummy_date",
       "NameYear", "KeyYear"] +
      [c for c in last_df.columns if c.startswith("Unnamed:")] +
      date_cols
)
last_df.drop(columns=[c for c in cols_to_drop if c in last_df.columns], inplace=True)




<ipython-input-73-3045701164>:62: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_df["Target"] = (
<ipython-input-73-3045701164>:76: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_df.drop(columns=[c for c in cols_to_drop if c in last_df.columns], inplace=True)


In [74]:
last_df.head()

Tax code number  Registered office address - Postal code  Registered office address - Longitude  Registered office address - Latitude  Trading address - Postal code Legal status                       Legal form Company category Incorporation year  No of available years Last accounting closing date Event 0 Event -1 Event -2 Event -3 Event -4 Event -5 Event -6                                      Company name  Year  0001_Revenues from sales and services  0002_EBITDA  0002_Revenues from sales and services  0003_Profit (loss)  0004_Total assets  0005_Total shareholder's funds  0006_Net financial position 0007_EBITDA/Vendite 0008_Return on sales (ROS)  0009_Return on asset (ROA) 0010_Return on equity (ROE) 0011_Debt/equity ratio 0012_Banks/turnover 0013_Debt/EBITDA ratio 0014_Total assets turnover (times)  0015_Number of employees  0016_TOTAL receivables due from shareholders  0017_Called share capital  0018_TOTAL FIXED ASSETS  0019_TOTAL INTANGIBLE FIXED ASSETS  0020_Start-up and expansion costs  0021_Research and dev. exp.  0022_Ind. patents and intellect. property rights  0023_Concessions, licenses, trademarks and similar rights  0024_Goodwill/Consolidation Difference  0025_including: Goodwill  0026_Additions in progress and advances  0027_Additions in progress and advances  0027_Others  0028_(Amortization provision)  0029_TOTAL TANGIBLE FIXED ASSETS  0030_including: leased tangible assets  0031_Land and buildings  0032_Plant and machinery  0033_Indust. and commercial equipment  0034_Other assets  0035_(Depreciation provision)  0036_TOTAL FINANCIAL FIXED ASSETS  0037_including: short term  0038_Total equity investments  0039_Subsidiary companies  0040_Associated companies  0041_Parent companies  0042_Companies under parent companies control  0043_Other companies  0044_Total Receivables  0045_Receiv. due from subs. Comp.  0046_Receiv. due from subs. Comp.  0046_Receiv. due from subs. companies - beyond 12 months  0047_Receiv. due from assoc. companies  0048_Receiv. due from assoc. companies - beyond 12 months  0049_Receiv. due from parent comp. - beyond 12 months  0050_Due from comp. under parent companies control  0050_Receiv. due from parent comp. - beyond 12 months  0051_Due from comp. under parent companies control  0051_Due from comp. under parent companies control - beyond 12 months  0052_Due from comp. under parent companies control - beyond 12 months  0052_Receiv. due from other comp.  0053_Receiv. due from others - beyond 12 months  0054_FIN. RECEIV. WITHIN 12 MONTHS  0054_Receiv. due from others - beyond 12 months  0055_FINA. RECEIV. BEYOND 12 MONTHS  0056_Other securities  0057_Other securities  0057_Own shares  0058_Derivatives  0058_Own shares  0059_Derivatives  0059_Own shares: par value  0060_Own shares: par value  0060_TOTAL CURRENT ASSETS  0061_TOTAL INVENTORIES  0062_Raw and consumable materials  0063_Work in progress and semifinished products  0064_Contract work in progress  0065_Finished products and goods  0066_Advances  0067_Advances  0067_Tangible fixed assets to be sold  0068_TOTAL RECEIVABLES  0069_Trade accounts  0070_Trade accounts - beyond 12 months  0071_Receiv. due from subs. comp. - beyond 12 months  0072_Receiv. due from assoc. Comp.  0073_Receiv. due from assoc. Comp. - beyond 12 months  0074_Receiv. due from parent comp.  0075_Tax receivables  0076_Tax receiv. - beyond 12 months  0077_Tax receiv. for prepaid taxes  0078_Tax receiv. for prepaid taxes - beyond 12 months  0079_Receiv. due from others  0080_RECEIV. DUE WITHIN 12 MONTHS  0082_RECEIV. DUE BEYOND 12 MONTHS  0083_TOTAL FINANCIAL ASSETS  0084_Invest. in subs. comp.  0085_Invest. in assoc. comp.  0086_Invest. in parent comp.  0087_Invest. in comp. under parent companies control  0088_Other investments  0089_Financial instruments for cash pooling  0090_TOTAL LIQUID FUNDS  0091_Bank and postal deposits  0092_Checks  0093_Cash and cash equivalents  0094_Cash and cash equivalents  0094_TOTAL ACCRUED INCOME AND PREPAID EXPENSES  0095_Accrued in